<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Christoph Berke </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Statistische Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060">&Uuml;bungsblatt 1</h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Wintersemester 23/24</h3>


<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml</a></font>

<font size="4" color="#606060">**Abgabe**: <span style="color:#82a8cf"> 16.10.2023, 10:00 Uhr </span> <span style="float:right;">**Besprechung**: 17.10.2023 </span></font>

<font size="4" color="#606060">**Name**: <span style="color:#82a8cf"> Bitte geben Sie Ihren Namen an.  </span> </font>

<table style="border-style: none; width: 100%; background-color: #FFFFFF"><tr style="border-style: none;">
<td style="border-style: none; width:2%; text-align: left; font-size: 25px; font-weight: 200;background-color: #FFFFFF">Aufgabe 6: Thermalisierung eines Gittergases </td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 15px;background-color: #FFFFFF">[6 + 4 = 10 Punkte]</td></tr></table>

In [ ]:
using GLMakie, Random

In [ ]:
# Diese Funktion erzeugt eine Anfangskonfiguration, in der auf dem Teilquadrat der 
# Größe Linit x Linit in der Ecke des größeren Gitters mit Lfinal x Lfinal Punkte
# der Anteil filling der Gitterplätze zufällig besetzt sind (d.h. den Wert 1 haben).
# Rückgabewert sind das Gitter, sowie die Indizes der besetzten Plätze.
function initialize_lattice(Linit, Lfinal, filling)
    
    lattice = zeros(Bool, Lfinal, Lfinal) # Gitterpunkte, 0 wenn unbesetzt, 1 wenn besetzt
    lattice[1:Linit, 1:Linit] = (rand(Linit, Linit) .< filling) # Erzeuge Zufallsmatrix mit gewünschter Füllung
    
    return lattice, findall(lattice) # Rueckgabe des Gitters, sowie der Indizes der Einträge mit Wert 1.
end

In [ ]:
# Funktion soll einen Update-Schritt ausführen: 
# (i)  zufälliges Teilchen auswählen 
# (ii) zufällige Richtung (oben,unten,links,rechts) auswählen
# (iii) versuchen, das Teilchen in die Richtung zu bewegen (siehe Aufgabenblatt)
# (iv) lattice und indices updaten, wenn Schritt (iii) erfolgreich ist.
# Die Variable lattice speichert das Gitterarray, die Variable indices die Indizes der von Null
# verschiedenen Einträge und die Variable L_current die Größe des zugänglichen Gitters 
# (für Aufgabebteil a) ist das einfach die Dimension von lattice in x- oder y-Richtung)
function update!(lattice, indices, L_current)
    
    ### Schritt (i) ###
    p = rand(1:size(indices,1)) # waehle eine zufaelliges Teilchen aus
    x, y = Tuple(indices[p])    # aktuelle Koordinaten finden
    
    nx, ny = -1, -1 # potenziell neue Koordinaten des Teilchens
    
    #################################################
    # Ergänzen Sie hier die Schritte (ii) und (iii) #
    #################################################    
    # Diesen Code hier sollen sie ersetzen  #
    shuffle!(lattice)                       #
    #########################################
    
    
    ### Schritt (iv) ###
    # Gegebenenfalls Update des Gitterarrays und des Arrays, in dem die Positionen gespeichert sind.
    # lattice[x, y], lattice[nx, ny] = lattice[nx, ny], lattice[x, y]
    # Update der Koordinaten
    # indices[p] = CartesianIndex(nx,ny)
    
    return
end

## a) Thermalisierung des Gittergases

In [ ]:
# Variablen für Gesamtgittergröße, Anfangsgittergröße, Filling
Ltot, Linit, fillfrac = 120, 30, 0.4

# Erzeuge Gitter lat und Array pos, das die aktuellen Indizes der Gasteilchen speichert.
lat, pos = initialize_lattice(Linit,Ltot,fillfrac);
lat, pos = Observable(lat), Observable(pos)

# Figure und Achsenumgebung erzeugen. Anfangskonfiguration darstellen.
fig = Figure()
ax = Axis(fig[1,1:2], aspect = DataAspect())
hm = heatmap!(ax, lat, colormap = :binary)
hidedecorations!(ax)

# Start/Stop Button
run = Button(fig[2,1]; label = "Start / Stop", tellwidth = false)
isrunning = Observable(false)
on(run.clicks) do clicks; isrunning[] = !isrunning[]; end

# Restart Button
restart = Button(fig[2,2]; label = "Restart", tellwidth = false)
on(restart.clicks) do clicks; lat[], pos[] = initialize_lattice(Linit,Ltot,fillfrac) end
    
# Schleife die dauerhaft läuft, wenn isrunning[] == true
on(run.clicks) do clicks
    @async while isrunning[]
        isopen(fig.scene) || break # Stoppen wenn Fenster geschlossen ist.
        
        # Update Gitter
        for _ in 1:1_000 # Kann auf 10_000 erhöht werden für schnellere Thermalisierung.
            update!(lat[],pos[],Ltot)
        end
        notify(lat)        
        sleep(0.001)
    end
end

# Anzeige der Figure.
display(fig)

## b) Thermalisierung mit elastischen Wänden